In [1]:
import os, sys, time
from time import sleep
from pathlib import Path
import fnmatch, glob, shutil

In [2]:
import pandas as pd
import numpy as np
from pandas import Series, DataFrame

In [3]:
import logging

In [4]:
time_start = pd.Timestamp.now()

### was: `C:/SDS/SDS_glob_for_rev_nums.log`

In [5]:
try: #{
    logging.basicConfig(level=logging.INFO,
                        filename="C:/SDS/SDS_glob_for_rev_nums.log",
                        format='%(asctime)s - %(message)s - %(lineno)s',
                        datefmt='%Y-%m-%d-%H%M%S',
                        filemode='w')
#}
except: #{
    errorMessage = str(sys.exc_info()[0]) + "\n\t\t"
    errorMessage = errorMessage + str(sys.exc_info()[1]) + "\n\t\t"
    errorMessage = errorMessage + str(sys.exc_info()[2]) + "\n"
    exc_type, exc_obj, exc_tb = sys.exc_info()
    fname = os.path.split(exc_tb.tb_frame.f_code.co_filename)[1]
    typeE = str("TYPE : " + str(exc_type))
    fileE = str("FILE : " + str(fname))
    lineE = str("LINE : " + str(exc_tb.tb_lineno))
    messageE = str("MESG : " + "\n" + str(errorMessage) + "\n")
    print("\n" + typeE +
          "\n" + fileE +
          "\n" + lineE +
          "\n" + messageE)
#}
else: #{
    print("[SETUP-LOGGER] FIN...")
#}

[SETUP-LOGGER] FIN...


### *DEFINE DIRECTORIES*

In [6]:
in_directory = Path("J:/controlled_docs/SDS/Agilent_SDS/")

In [7]:
out_directory = Path("J:/controlled_docs/SDS/In Process-DO NOT Use/")

In [8]:
in_file = "C:/data/inbound/052019_All products SDS except OEM.xlsx"

### *DEFINE FUNCTIONS*

In [9]:
def create_country_sds(the_out_directory, the_country_name, the_file): #{
    try: #{
        # CREATE 'in-place' VARIABLE FOR COUNTRY_DIR
        test_country_dir = os.path.join(str(the_out_directory), str(the_country_name))
        # CREATE COUNTRY DIRECTORY IF IT DOES NOT EXIST
        if not os.path.exists(test_country_dir): #{
            # MAKE IT EXIST!
            os.makedirs(test_country_dir)
            print(str(the_country_name) + " == DID NOT EXIST! DOES MEOW!")
        #}
        # CREATE NEW PATH VARIABLE FROM INPUT PARAMETERS
        the_new_path = os.path.join(test_country_dir, str(the_file))
        print("NEW-PATH == " + str(the_new_path))
        
        return Path(the_new_path)
    #}
    except: #{
        errorMessage = str(sys.exc_info()[0]) + "\n\t\t"
        errorMessage = errorMessage + str(sys.exc_info()[1]) + "\n\t\t"
        errorMessage = errorMessage + str(sys.exc_info()[2]) + "\n"
        exc_type, exc_obj, exc_tb = sys.exc_info()
        fname = os.path.split(exc_tb.tb_frame.f_code.co_filename)[1]
        typeE = str("TYPE : " + str(exc_type))
        fileE = str("FILE : " + str(fname))
        lineE = str("LINE : " + str(exc_tb.tb_lineno))
        messageE = str("MESG : " + "\n" + str(errorMessage) + "\n")
        print("\n" + typeE +
              "\n" + fileE +
              "\n" + lineE +
              "\n" + messageE)
    #}
    else: #{
        print("FIN...")
    #}
#}

In [10]:
test_return = create_country_sds(the_out_directory=out_directory,
                                the_country_name="Daves House",
                                the_file="poop.txt")

NEW-PATH == J:\controlled_docs\SDS\In Process-DO NOT Use\Daves House\poop.txt


In [11]:
print(test_return)

J:\controlled_docs\SDS\In Process-DO NOT Use\Daves House\poop.txt


# `idx_file`

In [12]:
idx_file = "C:/SDS/SDS-revs.txt"

In [13]:
old_path_list = []
new_path_list = []
file_name_list = []

# `Index` from file

In [14]:
# open a file
fo = open(idx_file, "r")

In [15]:
with open(idx_file) as f: #{
    content = f.readlines()
#}
# you may also want to remove whitespace characters like `\n` at the end of each line
content = [x.strip() for x in content]

In [16]:
fo.close()

In [17]:
print("NUMBER WITHIN INDEX: \n" + str(len(content)))

NUMBER WITHIN INDEX: 
0


In [18]:
# Define initial DataFre
dfSDS = pd.read_excel(str(in_file), parse_data=True, dtype=np.str,
                      sheet_name=0, header=0, index_cols=2, usecols=[2])
logging.info(dfSDS.describe())

In [19]:
# SETUP INDEX
idx_sds = pd.Index(dfSDS['SDS PN'])

# `glob`

In [ ]:
rev_save_list = []
new_path_list = []

try: #{
    # iterature thru directory/directories
    for root, d_names, f_names, in os.walk(in_directory): #{
        # if there are files in directory
        if len(f_names) >= 0: #{
            # for each file <<PERFORM THE FOLLOWING ACTIONS>>
            for file in f_names: #{
                print(file)
                # ASSEMBLE!
                file_path = os.path.join(root, file)
                #print(file_path)
                file_name = str(os.path.basename(file_path))
                country_name = str(os.path.dirname(file_path))
                country_name = os.path.basename(country_name)
                print("COUNTRY-NAME == " + country_name)
                # PERFORM SUB-STR OPERATIONS
                theStr = str(file_path)
                theLen = len(theStr)
                idxMrk = theStr.rfind('\\', 0, theLen)
                idxMrk += 1 # to offset '\' above
                endMrk = theStr.find('_', idxMrk, theLen)
                pnStr = str(theStr[idxMrk:endMrk])
                if (idx_sds.contains(pnStr)) & (fnmatch.fnmatch(file, '*[_][0-9].pdf')):  # {
                    no_rev = file_name[:len(file_name)-5]
                    ####################################
                    ## READ IN IDX FILE EVERY TIME YO ##
                    ####################################
                    with open(idx_file) as f: #{
                        content = f.readlines()
                    #}
                    # you may also want to remove whitespace
                    # chars like `\n` at the end of each line
                    content = [x.strip() for x in content]
                    fo.close()
                    # SETUP PANDAS INDEX VAR
                    idx = pd.Index(content)
                    ########################################
                    # CHECK IF WE ALREADY ADDED THIS 'file'#
                    ########################################
                    if idx.contains(no_rev) is True: #{
                        print("ALREADY ADDED " + str(file))
                    #}
                    else: #{
                        print("NOT ADDED YET! " + str(file))
                        # CREATE GLOB-LIST:
                        rev_list = glob.glob(str(os.path.join(root, no_rev) + "*"))
                        if len(rev_list) > 1: #{
                            print("HAS REVISION NUMBER!")
                            sorted_revs = sorted(rev_list)
                            test = sorted_revs.pop()
                            print("\t\t" + str(test))
                            #the_len = len(rev_list)
                            #print(the_len)
                            rev_save_list.append(test)
                            # WRITE TO IDX-FILE
                            fo = open(idx_file, "a")
                            fo.write("\n" + str(no_rev))
                            fo.close()
                            """
                            for name in sorted_revs: #{
                            print('    {}'.format(name))
                            #}
                            """                        
                        #}
                        else: #{
                            print("IS NEWEST REV# ALREADY!")
                            rev_save_list.append(file_path)
                            # CALL  FUNCTION TO GET PROPER VAR
                            new_path = create_country_sds(the_out_directory=out_directory,
                                                         the_country_name=str(country_name),
                                                         the_file=file)
                            new_path_list.append(new_path)
                            # COPY FILE --> CREATE 'NEW_PATH'
                            #shutil.copy2(file_path, new_path)
                        #}
                    #}
                #print(file_name)
                #}
                elif (idx_sds.contains(pnStr)) & (fnmatch.fnmatch(file, "*.pdf")): #{
                    print("doesnt have ten number!?!")
                    rev_save_list.append(file_path)
                    # CALL  FUNCTION TO GET PROPER VAR
                    new_path = create_country_sds(the_out_directory=out_directory,
                                                 the_country_name=str(country_name),
                                                 the_file=file)
                    new_path_list.append(new_path)
                    # COPY FILE --> CREATE 'NEW_PATH'
                    #shutil.copy2(file_path, new_path)
                #}
                else: #{
                    print("<< SKIP >>")
                #}
            #}
        #}
    #}
#}
except: #{
    errorMessage = str(sys.exc_info()[0]) + "\n\t\t"
    errorMessage = errorMessage + str(sys.exc_info()[1]) + "\n\t\t"
    errorMessage = errorMessage + str(sys.exc_info()[2]) + "\n"
    exc_type, exc_obj, exc_tb = sys.exc_info()
    fname = os.path.split(exc_tb.tb_frame.f_code.co_filename)[1]
    typeE = str("TYPE : " + str(exc_type))
    fileE = str("FILE : " + str(fname))
    lineE = str("LINE : " + str(exc_tb.tb_lineno))
    messageE = str("MESG : " + "\n" + str(errorMessage) + "\n")
    print("\n" + typeE +
                  "\n" + fileE +
                  "\n" + lineE +
                  "\n" + messageE)
#}
else: #{
    print("FIN...")
#}

061496-1_AU(EN)_2.pdf
COUNTRY-NAME == Australia
<< SKIP >>
061496-2_AU(EN)_2.pdf
COUNTRY-NAME == Australia
<< SKIP >>
1016TK-1_AU(EN)_2.pdf
COUNTRY-NAME == Australia
NOT ADDED YET! 1016TK-1_AU(EN)_2.pdf


C:\Users\derbates\anaconda3\lib\site-packages\ipykernel_launcher.py:26: FutureWarning: The 'contains' method is deprecated and will be removed in a future version. Use 'key in index' instead of 'index.contains(key)'
C:\Users\derbates\anaconda3\lib\site-packages\ipykernel_launcher.py:82: FutureWarning: The 'contains' method is deprecated and will be removed in a future version. Use 'key in index' instead of 'index.contains(key)'
C:\Users\derbates\anaconda3\lib\site-packages\ipykernel_launcher.py:43: FutureWarning: The 'contains' method is deprecated and will be removed in a future version. Use 'key in index' instead of 'index.contains(key)'


IS NEWEST REV# ALREADY!
NEW-PATH == J:\controlled_docs\SDS\In Process-DO NOT Use\Australia\1016TK-1_AU(EN)_2.pdf
1016TK_AU(EN)_.pdf
COUNTRY-NAME == Australia
doesnt have ten number!?!
NEW-PATH == J:\controlled_docs\SDS\In Process-DO NOT Use\Australia\1016TK_AU(EN)_.pdf
11130047_AU(EN)_.pdf
COUNTRY-NAME == Australia
<< SKIP >>
1221TK-1_AU(EN)_2.pdf
COUNTRY-NAME == Australia
NOT ADDED YET! 1221TK-1_AU(EN)_2.pdf
IS NEWEST REV# ALREADY!
NEW-PATH == J:\controlled_docs\SDS\In Process-DO NOT Use\Australia\1221TK-1_AU(EN)_2.pdf
1221TK_AU(EN)_.pdf
COUNTRY-NAME == Australia
doesnt have ten number!?!
NEW-PATH == J:\controlled_docs\SDS\In Process-DO NOT Use\Australia\1221TK_AU(EN)_.pdf
1232TK-1_AU(EN)_2.pdf
COUNTRY-NAME == Australia
NOT ADDED YET! 1232TK-1_AU(EN)_2.pdf
IS NEWEST REV# ALREADY!
NEW-PATH == J:\controlled_docs\SDS\In Process-DO NOT Use\Australia\1232TK-1_AU(EN)_2.pdf
1232TK_AU(EN)_.pdf
COUNTRY-NAME == Australia
doesnt have ten number!?!
NEW-PATH == J:\controlled_docs\SDS\In Process-DO

IS NEWEST REV# ALREADY!
NEW-PATH == J:\controlled_docs\SDS\In Process-DO NOT Use\Australia\52000_AU(EN)_2.pdf
53000_AU(EN)_2.pdf
COUNTRY-NAME == Australia
NOT ADDED YET! 53000_AU(EN)_2.pdf
HAS REVISION NUMBER!
		J:\controlled_docs\SDS\Agilent_SDS\Australia\53000_AU(EN)_3.pdf
53000_AU(EN)_3.pdf
COUNTRY-NAME == Australia
ALREADY ADDED 53000_AU(EN)_3.pdf
55000-P_AU(EN)_2.pdf
COUNTRY-NAME == Australia
<< SKIP >>
55000_AU(EN)_3.pdf
COUNTRY-NAME == Australia
NOT ADDED YET! 55000_AU(EN)_3.pdf
IS NEWEST REV# ALREADY!
NEW-PATH == J:\controlled_docs\SDS\In Process-DO NOT Use\Australia\55000_AU(EN)_3.pdf
55100_AU(EN)_1.pdf
COUNTRY-NAME == Australia
NOT ADDED YET! 55100_AU(EN)_1.pdf
HAS REVISION NUMBER!
		J:\controlled_docs\SDS\Agilent_SDS\Australia\55100_AU(EN)_2.pdf
55100_AU(EN)_2.pdf
COUNTRY-NAME == Australia
ALREADY ADDED 55100_AU(EN)_2.pdf
55400_AU(EN)_3.pdf
COUNTRY-NAME == Australia
NOT ADDED YET! 55400_AU(EN)_3.pdf
HAS REVISION NUMBER!
		J:\controlled_docs\SDS\Agilent_SDS\Australia\55400_AU

HAS REVISION NUMBER!
		J:\controlled_docs\SDS\Agilent_SDS\Australia\ALD-101-1_AU(EN)_3.pdf
ALD-101-1_AU(EN)_3.pdf
COUNTRY-NAME == Australia
ALREADY ADDED ALD-101-1_AU(EN)_3.pdf
ALD-554A-1_AU(EN)_2.pdf
COUNTRY-NAME == Australia
NOT ADDED YET! ALD-554A-1_AU(EN)_2.pdf
HAS REVISION NUMBER!
		J:\controlled_docs\SDS\Agilent_SDS\Australia\ALD-554A-1_AU(EN)_3.pdf
ALD-554A-1_AU(EN)_3.pdf
COUNTRY-NAME == Australia
ALREADY ADDED ALD-554A-1_AU(EN)_3.pdf
ALD-554DA-1_AU(EN)_2.pdf
COUNTRY-NAME == Australia
NOT ADDED YET! ALD-554DA-1_AU(EN)_2.pdf
HAS REVISION NUMBER!
		J:\controlled_docs\SDS\Agilent_SDS\Australia\ALD-554DA-1_AU(EN)_3.pdf
ALD-554DA-1_AU(EN)_3.pdf
COUNTRY-NAME == Australia
ALREADY ADDED ALD-554DA-1_AU(EN)_3.pdf
ALD-556X_AU(EN)_2.pdf
COUNTRY-NAME == Australia
NOT ADDED YET! ALD-556X_AU(EN)_2.pdf
HAS REVISION NUMBER!
		J:\controlled_docs\SDS\Agilent_SDS\Australia\ALD-556X_AU(EN)_3.pdf
ALD-556X_AU(EN)_3.pdf
COUNTRY-NAME == Australia
ALREADY ADDED ALD-556X_AU(EN)_3.pdf
ALD-8315-1_AU(EN)_3.p

...

IS NEWEST REV# ALREADY!
NEW-PATH == J:\controlled_docs\SDS\In Process-DO NOT Use\Brazil\PST-1171M1000_BR(PT-BR)_1.pdf
PST-1171_BR(PT-BR)_1.pdf
COUNTRY-NAME == Brazil
NOT ADDED YET! PST-1171_BR(PT-BR)_1.pdf
HAS REVISION NUMBER!
		J:\controlled_docs\SDS\Agilent_SDS\Brazil\PST-1171_BR(PT-BR)_2.pdf
PST-1171_BR(PT-BR)_2.pdf
COUNTRY-NAME == Brazil
ALREADY ADDED PST-1171_BR(PT-BR)_2.pdf
PST-1180A100A01_BR(PT-BR)_2.pdf
COUNTRY-NAME == Brazil
NOT ADDED YET! PST-1180A100A01_BR(PT-BR)_2.pdf
HAS REVISION NUMBER!
		J:\controlled_docs\SDS\Agilent_SDS\Brazil\PST-1180A100A01_BR(PT-BR)_3.pdf
PST-1180A100A01_BR(PT-BR)_3.pdf
COUNTRY-NAME == Brazil
ALREADY ADDED PST-1180A100A01_BR(PT-BR)_3.pdf
PST-1180B2000_BR(PT-BR)_1.pdf
COUNTRY-NAME == Brazil
NOT ADDED YET! PST-1180B2000_BR(PT-BR)_1.pdf
HAS REVISION NUMBER!
		J:\controlled_docs\SDS\Agilent_SDS\Brazil\PST-1180B2000_BR(PT-BR)_2.pdf
PST-1180B2000_BR(PT-BR)_2.pdf
COUNTRY-NAME == Brazil
ALREADY ADDED PST-1180B2000_BR(PT-BR)_2.pdf
PST-1180_BR(PT-BR)_2.pdf
CO

HAS REVISION NUMBER!
		J:\controlled_docs\SDS\Agilent_SDS\Brazil\PST-1215_BR(PT-BR)_3.pdf
PST-1215_BR(PT-BR)_3.pdf
COUNTRY-NAME == Brazil
ALREADY ADDED PST-1215_BR(PT-BR)_3.pdf
PST-1220M100A01_BR(PT-BR)_1.pdf
COUNTRY-NAME == Brazil
NOT ADDED YET! PST-1220M100A01_BR(PT-BR)_1.pdf
HAS REVISION NUMBER!
		J:\controlled_docs\SDS\Agilent_SDS\Brazil\PST-1220M100A01_BR(PT-BR)_2.pdf
PST-1220M100A01_BR(PT-BR)_2.pdf
COUNTRY-NAME == Brazil
ALREADY ADDED PST-1220M100A01_BR(PT-BR)_2.pdf
PST-1220_BR(PT-BR)_1.pdf
COUNTRY-NAME == Brazil
NOT ADDED YET! PST-1220_BR(PT-BR)_1.pdf
HAS REVISION NUMBER!
		J:\controlled_docs\SDS\Agilent_SDS\Brazil\PST-1220_BR(PT-BR)_2.pdf
PST-1220_BR(PT-BR)_2.pdf
COUNTRY-NAME == Brazil
ALREADY ADDED PST-1220_BR(PT-BR)_2.pdf
PST-1225M100A01_BR(PT-BR)_2.pdf
COUNTRY-NAME == Brazil
NOT ADDED YET! PST-1225M100A01_BR(PT-BR)_2.pdf
HAS REVISION NUMBER!
		J:\controlled_docs\SDS\Agilent_SDS\Brazil\PST-1225M100A01_BR(PT-BR)_3.pdf
PST-1225M100A01_BR(PT-BR)_3.pdf
COUNTRY-NAME == Brazil
ALRE

HAS REVISION NUMBER!
		J:\controlled_docs\SDS\Agilent_SDS\Brazil\PST-1275M100A01_BR(PT-BR)_3.pdf
PST-1275M100A01_BR(PT-BR)_3.pdf
COUNTRY-NAME == Brazil
ALREADY ADDED PST-1275M100A01_BR(PT-BR)_3.pdf
PST-1275_BR(PT-BR)_2.pdf
COUNTRY-NAME == Brazil
NOT ADDED YET! PST-1275_BR(PT-BR)_2.pdf
IS NEWEST REV# ALREADY!
NEW-PATH == J:\controlled_docs\SDS\In Process-DO NOT Use\Brazil\PST-1275_BR(PT-BR)_2.pdf
PST-1280K1000_BR(PT-BR)_1.pdf
COUNTRY-NAME == Brazil
NOT ADDED YET! PST-1280K1000_BR(PT-BR)_1.pdf
HAS REVISION NUMBER!
		J:\controlled_docs\SDS\Agilent_SDS\Brazil\PST-1280K1000_BR(PT-BR)_2.pdf
PST-1280K1000_BR(PT-BR)_2.pdf
COUNTRY-NAME == Brazil
ALREADY ADDED PST-1280K1000_BR(PT-BR)_2.pdf
PST-1280K100A01_BR(PT-BR)_1.pdf
COUNTRY-NAME == Brazil
NOT ADDED YET! PST-1280K100A01_BR(PT-BR)_1.pdf
HAS REVISION NUMBER!
		J:\controlled_docs\SDS\Agilent_SDS\Brazil\PST-1280K100A01_BR(PT-BR)_2.pdf
PST-1280K100A01_BR(PT-BR)_2.pdf
COUNTRY-NAME == Brazil
ALREADY ADDED PST-1280K100A01_BR(PT-BR)_2.pdf
PST-1280_BR

HAS REVISION NUMBER!
		J:\controlled_docs\SDS\Agilent_SDS\Brazil\PST-1325M100A01_BR(PT-BR)_3.pdf
PST-1325M100A01_BR(PT-BR)_3.pdf
COUNTRY-NAME == Brazil
ALREADY ADDED PST-1325M100A01_BR(PT-BR)_3.pdf
PST-1325_BR(PT-BR)_2.pdf
COUNTRY-NAME == Brazil
NOT ADDED YET! PST-1325_BR(PT-BR)_2.pdf
HAS REVISION NUMBER!
		J:\controlled_docs\SDS\Agilent_SDS\Brazil\PST-1325_BR(PT-BR)_5.pdf
PST-1325_BR(PT-BR)_3.pdf
COUNTRY-NAME == Brazil
ALREADY ADDED PST-1325_BR(PT-BR)_3.pdf
PST-1325_BR(PT-BR)_4.pdf
COUNTRY-NAME == Brazil
ALREADY ADDED PST-1325_BR(PT-BR)_4.pdf
PST-1325_BR(PT-BR)_5.pdf
COUNTRY-NAME == Brazil
ALREADY ADDED PST-1325_BR(PT-BR)_5.pdf
PST-1330M100A01_BR(PT-BR)_2.pdf
COUNTRY-NAME == Brazil
NOT ADDED YET! PST-1330M100A01_BR(PT-BR)_2.pdf
HAS REVISION NUMBER!
		J:\controlled_docs\SDS\Agilent_SDS\Brazil\PST-1330M100A01_BR(PT-BR)_3.pdf
PST-1330M100A01_BR(PT-BR)_3.pdf
COUNTRY-NAME == Brazil
ALREADY ADDED PST-1330M100A01_BR(PT-BR)_3.pdf
PST-1330_BR(PT-BR)_1.pdf
COUNTRY-NAME == Brazil
NOT ADDED YET! 

HAS REVISION NUMBER!
		J:\controlled_docs\SDS\Agilent_SDS\Brazil\PST-1380_BR(PT-BR)_2.pdf
PST-1380_BR(PT-BR)_2.pdf
COUNTRY-NAME == Brazil
ALREADY ADDED PST-1380_BR(PT-BR)_2.pdf
PST-1385A1000_BR(PT-BR)_1.pdf
COUNTRY-NAME == Brazil
NOT ADDED YET! PST-1385A1000_BR(PT-BR)_1.pdf
IS NEWEST REV# ALREADY!
NEW-PATH == J:\controlled_docs\SDS\In Process-DO NOT Use\Brazil\PST-1385A1000_BR(PT-BR)_1.pdf
PST-1385A100A01_BR(PT-BR)_2.pdf
COUNTRY-NAME == Brazil
NOT ADDED YET! PST-1385A100A01_BR(PT-BR)_2.pdf
HAS REVISION NUMBER!
		J:\controlled_docs\SDS\Agilent_SDS\Brazil\PST-1385A100A01_BR(PT-BR)_3.pdf
PST-1385A100A01_BR(PT-BR)_3.pdf
COUNTRY-NAME == Brazil
ALREADY ADDED PST-1385A100A01_BR(PT-BR)_3.pdf
PST-1385K1000_BR(PT-BR)_1.pdf
COUNTRY-NAME == Brazil
NOT ADDED YET! PST-1385K1000_BR(PT-BR)_1.pdf
HAS REVISION NUMBER!
		J:\controlled_docs\SDS\Agilent_SDS\Brazil\PST-1385K1000_BR(PT-BR)_2.pdf
PST-1385K1000_BR(PT-BR)_2.pdf
COUNTRY-NAME == Brazil
ALREADY ADDED PST-1385K1000_BR(PT-BR)_2.pdf
PST-1385K100A01_B

---

### *CHECK `LIST` VALUES/COUNTS*

In [ ]:
rev_save_list

In [ ]:
len(rev_save_list)

In [ ]:
new_path_list

In [ ]:
len(new_path_list)

### `TIMESTAMP`

In [ ]:
ts = pd.Timestamp.now()

In [ ]:
time_stamp_str = str(ts)

In [ ]:
time_stamp_str = time_stamp_str[:10]

In [ ]:
print(time_stamp_str)

---
##### DATAFRAME CREATION:

In [ ]:
# CREATE EMPTY DATAFRAME
df_test = pd.DataFrame()

In [ ]:
len(rev_save_list)

In [ ]:
# CREATE SERIES FROM LIST
n1 = pd.Series(new_path_list)

In [ ]:
df_test['New Location'] = n1

In [ ]:
df_test.to_csv("J:/controlled_docs/SDS/SDS Lists/SDS-Fixscan-"
              + time_stamp_str
              + ".csv")

# `2019_08_08`: changed dir of output_file

In [ ]:
df_test.head(15)

In [ ]:
time_end = pd.Timestamp.now()

In [ ]:
run_time = time_end - time_start

In [ ]:
logging.info("RUN-TIME == " + str(run_time))

In [ ]:
print(run_time)

In [ ]:
run_time.seconds

In [ ]:
run_time.seconds / 60 / 60